# LIMPIEZA DEL DATAFRAME DE METARS

## En este Notebook se va a realizar la limpieza de los partes METAR obtenidos anteriormente. El resultado final de la limpieza es un DataFrame con las siguientes columnas:

- **Metar_id**: Columna con un id único para cada parte Metar, para poder relacionarlo posteriormente con los vuelos.
- **Date_time**: Columna en formato *Datetime* con la fecha y la hora de emisión del parte.
- **Day**: Columna con el día en el que se emitió el parte en formato YYYY-MM-DD.
- **Hour**: Hora en la que se emitió el parte en formato HH:MM.
- **Condition**: Condición meteorológica del parte.
- **Temperature**: Temperatura en grados Celsius [º].
- **Wind**: Velocidad del viento en nudos o millas naúticas por hora [knots].
- **Gusts**: Velocidad de ráfagas si las hubiere en nudos o millas naúticas por hora [knots].
- **Relative_hum**: Humedad relativa en tanto por ciento [%].
- **Pressure**: Presión atmosférica en hectopascales [hPa].

In [1]:
import time
import numpy as np
import pylab as plt   
import seaborn as sns
import pandas as pd
import re
import sys
sys.path.append('../src')
from funmetar import *

## Se cargan y concatenan los datos de los meses de interés en el orden deseado

In [2]:
# met_oct_23 = pd.read_csv("../data/metar/metar_october_2023.csv")
# met_sep_23 = pd.read_csv("../data/metar/metar_september_2023.csv")
# met_aug_23 = pd.read_csv("../data/metar/metar_august_2023.csv")
# met_jul_23 = pd.read_csv("../data/metar/metar_july_2023.csv")
# met_jun_23 = pd.read_csv("../data/metar/metar_june_2023.csv")
# met_may_23 = pd.read_csv("../data/metar/metar_may_2023.csv")
# met_apr_23 = pd.read_csv("../data/metar/metar_april_2023.csv")
# met_mar_23 = pd.read_csv("../data/metar/metar_march_2023.csv")
# met_feb_23 = pd.read_csv("../data/metar/metar_february_2023.csv")
# met_jan_23 = pd.read_csv("../data/metar/metar_january_2023.csv")
# met_dec_22 = pd.read_csv("../data/metar/metar_december_2022.csv")
# met_nov_22 = pd.read_csv("../data/metar/metar_november_2022.csv")
mt = pd.read_csv("../data/metars/metars_2017_2022.csv")

In [ ]:
# mt = pd.concat([met_oct_23,met_sep_23,met_aug_23,met_jul_23,met_jun_23,met_may_23,
#                met_apr_23,met_mar_23,met_feb_23,met_jan_23,met_dec_22,met_nov_22])

In [3]:
mt.head()

Day   Hour Condition Temperature Wind Relative_hum  \
0  Wednesday 1 November 2017  00:00     Clear         10°    6          87%   
1  Wednesday 1 November 2017  00:30     Clear          9°    7          87%   
2  Wednesday 1 November 2017  01:00     Clear         10°    7          82%   
3  Wednesday 1 November 2017  01:30     Clear          9°    7          87%   
4  Wednesday 1 November 2017  02:00     Clear          9°    6          87%   

   Pressure  
0  1021 hPa  
1  1022 hPa  
2  1022 hPa  
3  1022 hPa  
4  1022 hPa

In [25]:
mt.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 91168 entries, 0 to 91167
Data columns (total 8 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   Day           91168 non-null  object 
 1   Hour          91168 non-null  object 
 2   Condition     91168 non-null  object 
 3   Temperature   91168 non-null  object 
 4   Wind          91168 non-null  object 
 5   Relative_hum  91168 non-null  object 
 6   Pressure      91168 non-null  float64
 7   gusts         91168 non-null  object 
dtypes: float64(1), object(7)
memory usage: 5.6+ MB


In [5]:
mt.shape

(91168, 7)

## Los valores de las ráfagas (cuando las hay) se encuentran desafortunadamente en la columna de "Pressure" tras la estracción.
## Por ello se crea una función (<span style="color:blue">generar_columna_gust</span>) que extraiga los valores en una nueva columna llamada "Gusts".

In [6]:
mt['gusts'] = mt['Pressure'].apply(generar_columna_gust)

In [ ]:
help(generar_columna_gust)

## La columna *Relative_hum* viene algo sucia tras la extracción ya que cuando en el registro hay ráfagas, en la columna aparece el símbolo ">" y el valor de la humedad ha quedado desplazado a la siguiente columna.

## Por ello, se crea una función (<span style="color:blue">fix_hum_column</span>) que corrija la columna cuando sea necesario.

In [7]:
mt['Relative_hum'] = mt.apply(fix_hum_column, axis=1)


## En la columna *Pressure* nos quedamos únicamente con el valor numérico de la presión.

In [21]:
pd.set_option('display.max_rows', None)
mt.Pressure[mt.Pressure.isna()] = 1014.0

C:\Users\daarr\AppData\Local\Temp\ipykernel_114472\2428074336.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  mt.Pressure[mt.Pressure.isna()] = 1014.0


In [16]:
mt['Pressure'] = mt['Pressure'].apply(lambda x: int(x[-8:-4]) if '-' not in x else None)

## En la columna *Wind*, en ocasiones viene el dato numérico de la velocidad del viento y en otros caso el string *"Calm"*. Corregimos la columna para que en esos casos ponga *"0"*.

In [23]:
mt['Wind'] = mt['Wind'].apply(lambda x: 0 if x=="Calm" else x)

## Hacemos un cambio de variable a nudos en las columnas *"Wind"* y *"gusts"*.

In [26]:
conversion = 1.852
mt['Wind'] = mt['Wind'].apply(lambda x: int(round(float(x)/conversion,0)))
mt['gusts'] = mt['gusts'].apply(lambda x: int(round(float(x)/conversion,0)))

## En la columna *Temperature* nos quedamos únicamente con el valor numérico de la temperatura.

In [27]:
mt['Temperature'] = mt['Temperature'].apply(lambda x: int(x[:-1]))

## Hay aún 5 registros (de más de 17000) en los que aún aparece el símbolo ">" en la columna *Relative_hum* .  Se decide reemplazar el valor de estos registros por la moda de la columna.

In [29]:
mt["Relative_hum"][mt.Relative_hum == ">"] = mt['Relative_hum'].mode().iloc[0]

C:\Users\daarr\AppData\Local\Temp\ipykernel_114472\3997667125.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  mt["Relative_hum"][mt.Relative_hum == ">"] = mt['Relative_hum'].mode().iloc[0]


## En la columna *Relative_hum* nos quedamos únicamente con el valor numérico( en tanto por ciento) de la humedad.

In [31]:
mt['Relative_hum'] = mt['Relative_hum'].apply(lambda x: int(x[:-1]) if x.endswith("%") else int(x))

In [36]:
# mt[mt['Relative_hum'] ==0]

In [32]:
mt.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 91168 entries, 0 to 91167
Data columns (total 8 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   Day           91168 non-null  object 
 1   Hour          91168 non-null  object 
 2   Condition     91168 non-null  object 
 3   Temperature   91168 non-null  int64  
 4   Wind          91168 non-null  int64  
 5   Relative_hum  91168 non-null  int64  
 6   Pressure      91168 non-null  float64
 7   gusts         91168 non-null  int64  
dtypes: float64(1), int64(4), object(3)
memory usage: 5.6+ MB


## Convertimos a formato DateTime las columnas *"Day"* y *"date_time"* para poder tener posteriormente la tabla ordenada cronológicamente.

In [37]:
mt['Day'] = pd.to_datetime(mt['Day'], format='%A %d %B %Y').dt.strftime('%Y-%m-%d')

In [38]:
mt['date_time'] = pd.to_datetime(mt['Day'] + ' ' + mt['Hour'])

In [39]:
mt.head()

Day   Hour Condition  Temperature  Wind  Relative_hum  Pressure  \
0  2017-11-01  00:00     Clear           10     3            87    1021.0   
1  2017-11-01  00:30     Clear            9     4            87    1022.0   
2  2017-11-01  01:00     Clear           10     4            82    1022.0   
3  2017-11-01  01:30     Clear            9     4            87    1022.0   
4  2017-11-01  02:00     Clear            9     3            87    1022.0   

   gusts           date_time  
0      0 2017-11-01 00:00:00  
1      0 2017-11-01 00:30:00  
2      0 2017-11-01 01:00:00  
3      0 2017-11-01 01:30:00  
4      0 2017-11-01 02:00:00

In [40]:
mt = mt.sort_values(by='date_time', ascending=False)
mt = mt.reset_index(drop = True)

In [41]:
mt[mt.duplicated()]

Empty DataFrame
Columns: [Day, Hour, Condition, Temperature, Wind, Relative_hum, Pressure, gusts, date_time]
Index: []

## Añadimos un *id* a cada registro, reordenamos las columnas de la tabla y corregimos algunos de sus nombres.

In [42]:
mt['Metar_id'] = range(1, len(mt) + 1)

In [43]:
reorder = ["Metar_id","date_time","Day","Hour","Condition","Temperature","Wind","gusts","Relative_hum","Pressure"]
mt = mt[reorder]

In [44]:
mt = mt.rename(columns ={'gusts':'Gusts', 'date_time':'Date_time'})


In [45]:
mt.shape

(91168, 10)

In [50]:
mt.groupby('Day').agg({"Metar_id":"count"}).sort_values(by = "Metar_id")

Metar_id
Day                 
2020-10-15        11
2018-05-28        21
2020-04-22        28
2020-10-13        30
2020-04-23        30
2020-09-09        36
2021-09-18        38
2022-05-25        39
2020-10-19        39
2018-05-02        42
2022-07-07        42
2020-01-13        42
2020-02-07        42
2020-11-27        42
2020-10-28        43
2021-03-29        43
2018-05-07        43
2022-07-06        43
2020-11-26        44
2020-11-25        44
2021-09-17        44
2018-03-25        44
2018-03-26        44
2022-03-27        44
2022-10-15        44
2020-09-11        44
2020-04-10        44
2020-03-29        44
2021-03-28        44
2018-04-10        44
2019-10-27        44
2020-08-26        44
2019-06-27        44
2021-09-22        45
2018-08-21        45
2021-03-30        45
2021-09-21        45
2019-09-18        45
2020-04-29        45
2019-02-07        45
2020-12-01        45
2021-03-22        45
2021-05-02        45
2019-04-14        46
2021-02-18        46
2021-02-17        46
2020-10-29        46
2022-08-11        46
2019-03-31        46
2020-09-10        46
2021-07-19        46
2019-04-01        46
2018-10-28        46
2022-10-30        46
2019-02-08        46
2020-03-21        46
2021-11-03        46
2017-12-01        46
2018-04-13        47
2021-12-16        47
2022-01-20        47
2020-07-04        47
2019-09-11        47
2018-11-23        47
2019-09-10        47
2018-11-26        47
2021-02-27        47
2021-06-04        47
2021-05-25        47
2022-06-22        47
2022-01-16        47
2019-05-18        47
2020-08-25        47
2018-10-12        47
2021-11-24        47
2020-08-16        47
2019-06-11        47
2020-08-08        47
2020-10-06        47
2021-03-03        47
2019-12-12        47
2022-05-23        47
2018-11-13        47
2022-07-22        47
2018-05-24        47
2018-04-08        47
2018-03-04        47
2018-04-23        47
2019-02-27        47
2021-09-07        47
2018-06-28        47
2020-03-05        47
2019-02-13        47
2022-11-18        47
2018-07-03        47
2017-11-16        47
2019-02-15        47
2017-11-18        47
2021-08-23        47
2017-11-22        47
2021-07-07        47
2018-08-09        47
2018-07-16        47
2020-02-24        47
2019-03-13        47
2017-12-29        47
2019-03-07        47
2021-07-31        47
2017-11-03        47
2018-01-23        47
2021-10-05        47
2022-12-26        47
2018-01-21        47
2021-02-15        47
2022-03-01        47
2021-01-01        47
2020-04-17        47
2020-06-11        47
2019-03-25        47
2019-01-29        47
2021-09-19        47
2022-04-07        47
2021-03-24        48
2021-03-17        48
2021-03-18        48
2021-03-19        48
2021-01-17        48
2021-01-15        48
2021-01-10        48
2021-01-12        48
2021-03-26        48
2021-01-14        48
2021-01-13        48
2021-03-27        48
2021-03-21        48
2021-03-25        48
2021-03-23        48
2021-03-20        48
2021-01-11        48
2021-02-24        48
2021-03-16        48
2021-02-26        48
2021-02-28        48
2021-03-01        48
2021-02-23        48
2021-02-22        48
2021-02-20        48
2021-02-19        48
2021-03-02        48
2021-02-16        48
2021-03-05        48
2021-02-14        48
2021-02-13        48
2021-03-06        48
2021-02-12        48
2021-03-07        48
2021-02-10        48
2021-02-03        48
2021-03-15        48
2021-01-23        48
2021-03-14        48
2021-01-24        48
2021-01-25        48
2021-01-31        48
2021-01-18        48
2021-02-25        48
2021-02-01        48
2021-03-12        48
2021-03-11        48
2021-03-10        48
2021-03-09        48
2021-03-08        48
2021-03-13        48
2017-11-01        48
2021-04-24        48
2021-04-01        48
2021-06-29        48
2021-06-28        48
2021-06-27        48
2021-06-26        48
2021-06-25        48
2021-06-24        48
2021-06-23        48
2021-06-22        48
2021-06-21        48
2021-06-20        48
2021-06-19        48
2021-06-15        48
2021-06-14        48
2

## Exportamos los datos limpios en formato *csv* y *parquet*.

In [51]:
mt2 = pd.read_csv("../data/metars/metars.csv")

In [52]:
mt = pd.concat([mt,mt2])

In [59]:
mt.columns

Index(['Metar_id', 'Date_time', 'Day', 'Hour', 'Condition', 'Temperature',
       'Wind', 'Gusts', 'Relative_hum', 'Pressure'],
      dtype='object')

In [69]:
columnas_a_verificar=['Day', 'Hour', 'Condition', 'Temperature',
       'Wind', 'Gusts', 'Relative_hum', 'Pressure']
mt[mt.duplicated(subset=columnas_a_verificar, keep='first')]

Empty DataFrame
Columns: [Metar_id, Date_time, Day, Hour, Condition, Temperature, Wind, Gusts, Relative_hum, Pressure]
Index: []

In [73]:
mt = mt.drop_duplicates(subset=columnas_a_verificar)

In [74]:
mt.shape

(108890, 10)

In [78]:
mt.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 108890 entries, 0 to 17721
Data columns (total 10 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   Metar_id      108890 non-null  int64  
 1   Date_time     108890 non-null  object 
 2   Day           108890 non-null  object 
 3   Hour          108890 non-null  object 
 4   Condition     108890 non-null  object 
 5   Temperature   108890 non-null  int64  
 6   Wind          108890 non-null  int64  
 7   Gusts         108890 non-null  int64  
 8   Relative_hum  108890 non-null  int64  
 9   Pressure      108890 non-null  float64
dtypes: float64(1), int64(5), object(4)
memory usage: 9.1+ MB


In [77]:
mt.Date_time.value_counts()

2022-12-31 23:30:00    1
2018-11-20 23:00:00    1
2018-11-21 00:00:00    1
2018-11-21 00:30:00    1
2018-11-21 01:00:00    1
2018-11-21 01:30:00    1
2018-11-21 02:00:00    1
2018-11-21 02:30:00    1
2018-11-21 03:00:00    1
2018-11-21 03:30:00    1
2018-11-21 04:00:00    1
2018-11-21 04:30:00    1
2018-11-21 05:00:00    1
2018-11-21 05:30:00    1
2018-11-21 06:00:00    1
2018-11-21 06:30:00    1
2018-11-21 07:00:00    1
2018-11-21 07:30:00    1
2018-11-21 08:00:00    1
2018-11-21 08:30:00    1
2018-11-21 09:00:00    1
2018-11-21 09:30:00    1
2018-11-21 10:00:00    1
2018-11-21 10:30:00    1
2018-11-21 11:00:00    1
2018-11-20 23:30:00    1
2018-11-20 22:30:00    1
2018-11-22 14:00:00    1
2018-11-20 22:00:00    1
2018-11-20 10:30:00    1
2018-11-20 11:00:00    1
2018-11-20 11:30:00    1
2018-11-20 12:00:00    1
2018-11-20 12:30:00    1
2018-11-20 13:00:00    1
2018-11-20 13:30:00    1
2018-11-20 14:00:00    1
2018-11-20 14:30:00    1
2018-11-20 15:00:00    1
2018-11-20 15:30:00    1


In [80]:
mt['Date_time'] = pd.to_datetime(mt['Date_time'], errors='coerce')
mt = mt.sort_values(by='Date_time', ascending=False)
mt = mt.reset_index(drop = True)
mt['Metar_id'] = range(1, len(mt) + 1)
mt.tail()

Metar_id           Date_time         Day   Hour Condition  \
108885    108886 2017-11-01 02:00:00  2017-11-01  02:00     Clear   
108886    108887 2017-11-01 01:30:00  2017-11-01  01:30     Clear   
108887    108888 2017-11-01 01:00:00  2017-11-01  01:00     Clear   
108888    108889 2017-11-01 00:30:00  2017-11-01  00:30     Clear   
108889    108890 2017-11-01 00:00:00  2017-11-01  00:00     Clear   

        Temperature  Wind  Gusts  Relative_hum  Pressure  
108885            9     3      0            87    1022.0  
108886            9     4      0            87    1022.0  
108887           10     4      0            82    1022.0  
108888            9     4      0            87    1022.0  
108889           10     3      0            87    1021.0

In [83]:
mt.head()

Metar_id           Date_time         Day   Hour Condition  Temperature  \
0         1 2023-10-31 23:30:00  2023-10-31  23:30      Fair            8   
1         2 2023-10-31 23:00:00  2023-10-31  23:00      Fair            8   
2         3 2023-10-31 22:30:00  2023-10-31  22:30      Fair            8   
3         4 2023-10-31 22:00:00  2023-10-31  22:00     Clear            8   
4         5 2023-10-31 21:30:00  2023-10-31  21:30     Clear            8   

   Wind  Gusts  Relative_hum  Pressure  
0     3      0            93    1017.0  
1     1      0            87    1017.0  
2     0      0            93    1017.0  
3     0      0            93    1017.0  
4     0      0            93    1017.0

In [84]:
mt.to_csv("../data/metars/metars_2017_2023.csv", index=False)

In [ ]:
mt.to_parquet('../data/metar/metar.gz', compression='gzip', index = False)